# Machine learning non-supervisé et réduction de dimension 

Ce notebook reprend des éléments de https://scikit-learn.org/stable/auto_examples/datasets/plot_iris_dataset.html et d'autres exemples de la documentation de scikit-learn, d'après une adaptation de Rémi Gribonval

In [ ]:
import sklearn
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt 

# Préliminaires: 
## Chargement de données : IRIS
On commence comme lors de la séance 1 par charger le jeu de données IRIS. Rappelons qu'IRIS rassemble des données mesurant les dimensions (longueur, largeur) des pétales et sépales de différents échantillons de trois variétés d'iris (Setosa, Versicolour, Virginica)

In [ ]:
from sklearn.datasets import load_iris
iris = load_iris()

In [ ]:
X = iris.data  
y = iris.target 

### Question 1: Quel est le nombre $n$ d'exemples ce jeu de données ? La dimension $d$ des exemples ?

In [ ]:
X.shape

## Conversion de format
Par la suite il sera pratique de bénéficier des fonctionnalités de pandas utilisée lors de la Séance 2 pour visualiser le contenu de jeux de données. La fonction de conversion suivante (issue de https://stackoverflow.com/questions/38105539/how-to-convert-a-scikit-learn-dataset-to-a-pandas-dataset) pourra nous resservir.

In [ ]:
def sklearn_to_df(sklearn_dataset):
    df = pd.DataFrame(sklearn_dataset.data, columns=sklearn_dataset.feature_names)
    df['target'] = pd.Series(sklearn_dataset.target)
    return df

Appliquons-là à notre jeu de données

In [ ]:
df_iris = sklearn_to_df(iris)

### Question 2: Inspection des données
Rappelez-vous la séance d'hier, que proposez-vous pour un premier aperçu de la structure des données ?

In [ ]:
df_iris.head()

In [ ]:
df_iris.describe()

### Question 3: quelle variable contient la classe (le type d'iris) ? Combien de classes et combien d'exemples par classes y a-t-il ? 

In [ ]:
df_iris['target'].value_counts()

# Partie 1 - réduction de dimension
## Première visualisation des données
On aimerait maintenant visualiser nos données. La fonction suivante permet d'afficher un jeu de données en 2d. La couleur indique la classe (Setosa, Versicolour, Virginica)

In [ ]:
def plot2d(X,y,label=['first','second']): # affichage d'un tableau nx2 de données X avec des couleurs déterminées par y de taille nx1
    x_min, x_max = X[:, 0].min() - 0.5, X[:, 0].max() + 0.5
    y_min, y_max = X[:, 1].min() - 0.5, X[:, 1].max() + 0.5
    plt.figure(figsize=(4, 3))
    plt.clf()
    # Plot the training points
    plt.scatter(X[:, 0], X[:, 1], c=y, cmap=plt.cm.Set1, edgecolor="k")
    plt.xlabel(label[0])
    plt.ylabel(label[1])
    plt.xlim(x_min, x_max)
    plt.ylim(y_min, y_max)
    plt.xticks(())
    plt.yticks(())

Pour utiliser cette fonction on a besoin des labels des colonnes de X

In [ ]:
labels = df_iris.columns; labels

## Question 4: quel problème a-t-on pour afficher le jeu de données ? Que proposez-vous ?

In [ ]:
plot2d(X[:,:2],y,labels[:2])

In [ ]:
plot2d(X[:,2:4],y,labels[2:4])

## Sélection de caractéristiques
Ce qu'on vient de faire est de la réduction de dimension par *sélection de caractéristiques !*
Pour aller plus loin (non couvert dans cette formation) il existe des méthodes automatisées de sélection de caractéristiques
Voir https://scikit-learn.org/stable/modules/feature_selection.html pour plus de détails

In [ ]:
X.shape

In [ ]:
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import chi2
X_new = SelectKBest(chi2, k=2).fit_transform(X, y)
X_new.shape

In [ ]:
plot2d(X_new,y)

-----
## Analyse en composantes principales
### Premier contact

In [ ]:
from sklearn.decomposition import PCA

X_reduced = PCA(n_components=3).fit_transform(iris.data)

In [ ]:
# To getter a better understanding of interaction of the dimensions
# plot the first three PCA dimensions
fig = plt.figure(1, figsize=(8, 6))
ax = fig.add_subplot(111, projection="3d", elev=-150, azim=110)

ax.scatter(
    X_reduced[:, 0],
    X_reduced[:, 1],
    X_reduced[:, 2],
    c=y,
    cmap=plt.cm.Set1,
    edgecolor="k",
    s=40,
)

ax.set_title("First three PCA directions")
ax.set_xlabel("1st eigenvector")
ax.xaxis.set_ticklabels([])
ax.set_ylabel("2nd eigenvector")
ax.yaxis.set_ticklabels([])
ax.set_zlabel("3rd eigenvector")
ax.zaxis.set_ticklabels([])

plt.show()

### Question 5 : pouvez-vous afficher les 2 premières composantes principales ? Et comparer avec le diagramme 2D obtenu en sélectionnant les deux premières caractéristiques de X ?

In [ ]:
plot2d(X_reduced[:,:2],y); plot2d(X[:,:2],y,labels[:2])

### Question 6: remarquez-vous ?

### Exercice à la maison: ACP et au-delà *en grande dimension*
https://scikit-learn.org/stable/auto_examples/decomposition/plot_faces_decomposition.html

### Pratique à la maison: approche non-linéaire avec tSNE sur IRIS
https://github.com/olekscode/Examples-PCA-tSNE/blob/master/Python/Visualizing%20Iris%20Dataset%20using%20PCA%20and%20t-SNE.ipynb

# Partie 2 : partitionnement
https://scikit-learn.org/stable/auto_examples/cluster/plot_cluster_iris.html

In [ ]:
from sklearn.cluster import KMeans

np.random.seed(5)

estimators = [
    ("k_means_iris_8", KMeans(n_clusters=8)),
    ("k_means_iris_3", KMeans(n_clusters=3)),
    ("k_means_iris_bad_init", KMeans(n_clusters=3, n_init=1, init="random")),
]

fignum = 1
titles = ["8 clusters", "3 clusters", "3 clusters, bad initialization"]
for name, est in estimators:
    fig = plt.figure(fignum, figsize=(4, 3))
    ax = fig.add_subplot(111, projection="3d", elev=48, azim=134)
    ax.set_position([0, 0, 0.95, 1])
    est.fit(X)
    labels = est.labels_

    ax.scatter(X[:, 3], X[:, 0], X[:, 2], c=labels.astype(float), edgecolor="k")

    ax.w_xaxis.set_ticklabels([])
    ax.w_yaxis.set_ticklabels([])
    ax.w_zaxis.set_ticklabels([])
    ax.set_xlabel("Petal width")
    ax.set_ylabel("Sepal length")
    ax.set_zlabel("Petal length")
    ax.set_title(titles[fignum - 1])
    ax.dist = 12
    fignum = fignum + 1

# Plot the ground truth
fig = plt.figure(fignum, figsize=(4, 3))
ax = fig.add_subplot(111, projection="3d", elev=48, azim=134)
ax.set_position([0, 0, 0.95, 1])

for name, label in [("Setosa", 0), ("Versicolour", 1), ("Virginica", 2)]:
    ax.text3D(
        X[y == label, 3].mean(),
        X[y == label, 0].mean(),
        X[y == label, 2].mean() + 2,
        name,
        horizontalalignment="center",
        bbox=dict(alpha=0.2, edgecolor="w", facecolor="w"),
    )
# Reorder the labels to have colors matching the cluster results
y = np.choose(y, [1, 2, 0]).astype(float)
ax.scatter(X[:, 3], X[:, 0], X[:, 2], c=y, edgecolor="k")

ax.w_xaxis.set_ticklabels([])
ax.w_yaxis.set_ticklabels([])
ax.w_zaxis.set_ticklabels([])
ax.set_xlabel("Petal width")
ax.set_ylabel("Sepal length")
ax.set_zlabel("Petal length")
ax.set_title("Ground Truth")
ax.dist = 12

fig.show()

## Pratique à la maison: cas où les k-moyennes ne fonctionnent pas ou mal
https://scikit-learn.org/stable/auto_examples/cluster/plot_kmeans_assumptions.html